# Seq2Seq model for text summarization

In [27]:
import torch
from torch.jit import script, trace
import torch.nn as nn
from torch import optim
import torch.nn.functional as F
import csv
import random
import re
import spacy
import os
import codecs
from io import open
import itertools
import math

In [28]:
USE_CUDA = torch.cuda.is_available()
device = torch.device("cuda:2" if USE_CUDA else "cpu")
SEED = 23

random.seed(SEED)
torch.manual_seed(SEED)

In [29]:
# choose directory to save trained model data if training is interupted
save_dir = os.path.join("preprocessed_data", "save")
# path to data files
train_path = "small_dataset_train.csv"
test_path = "small_dataset_test.csv"
val_path = "small_dataset_val.csv"
gensim_path = "../lt2212-v19-a4/GoogleNews-vectors-negative300.bin"
pre_trained = False # this is not implemented

Load Preprocesses Data
----------------------




In [30]:
import pandas as pd 

train_data = pd.read_csv(train_path) 
# Preview the first 5 lines of the loaded data 
train_data.head()

story  \
0  boston bombing suspect dzhokar tsarnaev tweete...   
1  23 year old exchange student attacked toronto ...   
2  robin lim american woman helped thousands poor...   
3  nations best military fliers wings clipped tha...   
4  decade following september 11 2001 attacks fou...   

                                          highlights  
0  new a cryptic tweet last august refers to the ...  
1  a friend in china sees the woman attacked in h...  
2  robin lim was named the 2011 cnn hero of the y...  
3  navys blue angels had 32 shows left in 2013 ai...  
4  reports alleged inappropriate cia involvement ...

In [31]:
# Default word tokens
PAD_token = 0  # Used for padding short sentences
SOS_token = 1  # Start-of-sentence token
EOS_token = 2  # End-of-sentence token
UNK_token = 3  # Unknown word token

PAD_str = '<pad>' 
SOS_str = '[START]'
EOS_str = '[END]'
UNK_str = '<unk>'

In [32]:
nlp = spacy.load('en_core_web_md')

class Vocab:
    def __init__(self, name):
        self.name = name
        self.trimmed = False
        self.word2index = {}
        self.word2count = {}
        self.embeddings = {}        
        self.index2word = {PAD_token: PAD_str, SOS_token: SOS_str, EOS_token: EOS_str, UNK_str: UNK_token}
        self.num_words = 4  # Count SOS, EOS, PAD, UNK        
        
    
    def addEmbedding(self,model,word): 
        vector = get_w2v_vectors(model, word)
        self.embeddings[word] = vector

    def addSentence(self, sentence):
        for word in sentence.split(' '):
            self.addWord(word)

    def addWord(self, word):
        if word not in self.word2index:
            self.word2index[word] = self.num_words
            self.word2count[word] = 1
            self.index2word[self.num_words] = word
            self.num_words += 1
        else:
            self.word2count[word] += 1

    # Remove words below a certain count threshold
    def trim(self, min_count):
        if self.trimmed:
            return
        self.trimmed = True
        keep_words = []
        for k, v in self.word2count.items():
            if v >= min_count:
                keep_words.append(k)

        print('keep_words {} / {} = {:.4f}'.format(
            len(keep_words), len(self.word2index), len(keep_words) / len(self.word2index)
        ))

        # Reinitialize dictionaries
        self.word2index = {}
        self.word2count = {}
        self.index2word = {PAD_token: PAD_str, SOS_token: SOS_str, EOS_token: EOS_str, UNK_str: UNK_token}
        self.num_words = 4 # Count default tokens

        for word in keep_words:
            self.addWord(word)

In [33]:
from gensim.models.keyedvectors import KeyedVectors
import numpy as np

def load_gensim_model(path_to_model):
    model =  KeyedVectors.load_word2vec_format(path_to_model, binary=True)
    return model

def get_w2v_vectors(w2v_model, words):
    w2v_vectors = {}
    for word in words:
        try:
            vec = w2v_model.word_vec(word)
            w2v_vectors[word] = vec
        # this exception will occur when a word does not exist in the vocabulary of this model
        except KeyError:
                vec = np.random.rand(1,300)[0]
    return w2v_vectors


In [34]:
# Using the functions defined above, return a populated vocab object and pairs list for the train data set
def loadPrepareVocab(train_data):
    import itertools as iter 
    print("Start preparing training data ...")      
    vocab = Vocab("CNN")
    t = train_data["story"].tolist()
    r = train_data["highlights"].tolist()
    # get the length of the longest sentence
    max_length = len(max(t, key=len).split(' '))
    # Split every line into pairs
    pairs = list(zip(t,r))
    if pre_trained:
        print("Loading gensim model...")
        gensim = load_gensim_model(gensim_path)
        print("Finished loading gensim model.")
    print("Counting word pairs and adding embedding vectors.")
    for pair in pairs:        
        vocab.addSentence(pair[0])
        vocab.addSentence(pair[1])    
        if pre_trained:
            vocab.addEmbedding(gensim,pair[0])
            vocab.addEmbedding(gensim,pair[1])        
    print("Counted words:", vocab.num_words)
    return vocab, pairs, max_length

vocab, pairs, max_length = loadPrepareVocab(train_data)

Start preparing training data ...
Counting word pairs and adding embedding vectors.
Counted words: 19790


In [35]:
# Add validation data to train
validation_data = pd.read_csv(val_path) 
# Preview the first 5 lines of the loaded data 
validation_data.head()

def addVal(validation_data):
    t = validation_data["story"].tolist()
    r = validation_data["highlights"].tolist()
    for words in list(zip(t,r)):     
        vocab.addSentence(words[0])
        vocab.addSentence(words[1]) 
addVal(validation_data)

In [36]:
# used to prepare validation data set to fit model (not finished)
def prepareData(data):
    print("Start preparing data ...") 
    t = data["story"].tolist()
    r = data["highlights"].tolist()
    pairs = list(zip(t,r))
    return pairs

In [37]:
# look at some examples
for pair in pairs[:2]:
    print("Story")
    print(pair[0])
    print("Highlight")
    print(pair[1])

Story
boston bombing suspect dzhokar tsarnaev tweeted since boston marathon bombings two friends tell cnn twitter account tweets included one 143 wednesday said stress free kind guy monday 804 pm hours bombings tweeted quote rapper jay z 1970s rb song love heart city tweet added stay safe people shortly midnight tuesday morning tweeted people know truth stay silent people speak truth hear cuz minority tsarnaev uses handle j_tsar describe profile reads salam aleikum greeting among muslims profile photo face lion mouth open baring fangs tweeted dozen times since bombing recent tweet one retweeted wednesday mufti ismail menk identifies muslim scholar attitude take away beauty matter good looking could enhance beauty making adorable tweet reads another tweet tsarnaev tuesday quote rapper eminem nowadays everybody wanna talk like got somethin say nothin comes move lips bunch gibberish another twitter account posted photo tuesday saying showed man going propose girlfriend marathon boston fou

# Prepare data

In [38]:
def indexesFromSentence(lang, sentence):
    sentence_indices = []
    for word in sentence.split(' '):
        try:
            sentence_indices.append(lang.word2index[word])
        except KeyError:
                sentence_indices.append(UNK_token)
    return sentence_indices + [EOS_token]

def embeddingsFromSentence(lang, sentence):
    sentence_embeddings = []
    for word in sentence.split(' '):
        try:
            sentence_embeddings.append(lang.embeddings[word])
        except KeyError:
                vec = np.random.rand(1,300)[0]
    return sentence_embeddings

def zeroPadding(l, fillvalue=PAD_token):
    return list(itertools.zip_longest(*l, fillvalue=fillvalue))

def binaryMatrix(l, value=PAD_token):
    m = []
    for i, seq in enumerate(l):
        m.append([])
        for token in seq:
            if token == PAD_token:
                m[i].append(0)
            else:
                m[i].append(1)
    return m

# Returns padded input sequence tensor and lengths
def inputVar(l, vocab):
    indexes_batch = [indexesFromSentence(vocab, sentence) for sentence in l]
    lengths = torch.tensor([len(indexes) for indexes in indexes_batch])
    padList = zeroPadding(indexes_batch)
    padVar = torch.LongTensor(padList)
    return padVar, lengths

# Returns padded target sequence tensor, padding mask, and max target length
def outputVar(l, vocab):
    indexes_batch = [indexesFromSentence(vocab, sentence) for sentence in l]
    max_target_len = max([len(indexes) for indexes in indexes_batch])
    padList = zeroPadding(indexes_batch)
    mask = binaryMatrix(padList)
    mask = torch.BoolTensor(mask)
    padVar = torch.LongTensor(padList)
    return padVar, mask, max_target_len

# Returns all items for a given batch of pairs
def batch2TrainData(vocab, pair_batch):
    pair_batch.sort(key=lambda x: len(x[0].split(" ")), reverse=True)
    input_batch, output_batch = [], []
    for pair in pair_batch:
        input_batch.append(pair[0])
        output_batch.append(pair[1])
    inp, lengths = inputVar(input_batch, vocab)
    output, mask, max_target_len = outputVar(output_batch, vocab)
    return inp, lengths, output, mask, max_target_len




In [39]:
# Look at examples of tensors and binary padding mask
small_batch_size = 2
batches = batch2TrainData(vocab, [random.choice(pairs) for _ in range(small_batch_size)])
input_variable, lengths, target_variable, mask, max_target_len = batches

print("input_variable:", input_variable)
print("lengths:", lengths)
print("target_variable:", target_variable)
print("mask:", mask)
print("max_target_len:", max_target_len)

input_variable: tensor([[12587,  2717],
        [ 1809,  1291],
        [   47,  1302],
        [ 8395,   603],
        [ 2236,  1889],
        [  629,   839],
        [ 1146,  7463],
        [ 5297,  3003],
        [  645,  8663],
        [ 3140,  2083],
        [ 2618,  2624],
        [  177, 11352],
        [  643,   787],
        [ 1195,  3798],
        [12014,  6353],
        [14692,  3832],
        [ 9449,   948],
        [ 2253,  1618],
        [12334,   468],
        [19768,  8663],
        [ 3530, 10227],
        [ 2183, 11353],
        [ 6913,  4839],
        [13682,  5521],
        [19768, 11354],
        [18772,  1947],
        [ 5796, 10261],
        [  464,  1988],
        [ 2253, 10823],
        [ 8801,  4603],
        [ 5888, 11353],
        [ 8108,   706],
        [ 2201,   338],
        [ 6949,  4960],
        [  371, 11355],
        [  979,    94],
        [ 1947, 11356],
        [11256,  2820],
        [ 3454,  5122],
        [ 2793, 11357],
        [19768, 11353],


Look at some examples. Make sure there are not too many UNK tokens, might have to include more words in vocab.

In [40]:
small_batch_size = 1
batches = batch2TrainData(vocab, [random.choice(pairs) for _ in range(small_batch_size)])
input_variable, lengths, target_variable, mask, max_target_len = batches

input_variable.size(), target_variable.size()
sample_source = input_variable.transpose(1,0)[0].data.cpu().numpy()
sample_target = target_variable.transpose(1,0)[0].data.cpu().numpy()

print("source:\n%s \n\ncorresponding tensor:\n%s \n" %(' '.join([vocab.index2word[o] for o in sample_source]), sample_source))
print("target:\n%s \n\ncorresponding tensor:\n%s \n" %(' '.join([vocab.index2word[o] for o in sample_target]), sample_target))

source:
travel warnings us department state stop faith hentschel 65 venturing iran may visit rustic sites ancient persepolis colorful bazaars tehran photo khaju bridge isfahan iran taken american traveler idea expect said hentschel spent two weeks iran booking trip private tour operator applying visa stunned friendliness iranian people alone makes want go back iran still relatively rare destination americans creating niche market handful tour operators across nation organize group trips travelers twice year news arrest three american backpackers along june election riots government crackdown iran may even harder sell travel companies said really depends political climate perception iran said mike mcdonnell operates site bestirantravelcom san francisco california site books trips non iranian travelers interested visiting site saw decline booking travel iran summer already really hard get iran first place officials us department state say travel warnings implemented iran since hostage cr

# Seq2Seq model

## Encoder

In [41]:
class EncoderRNN(nn.Module):
    def __init__(self, hidden_size, embedding, n_layers=1, dropout=0):
        super(EncoderRNN, self).__init__()
        self.n_layers = n_layers
        self.hidden_size = hidden_size
        self.embedding = embedding

        # Initialize GRU; the input_size and hidden_size params are both set to 'hidden_size'
        #   because the input size is a word embedding with number of features == hidden_size
        self.gru = nn.GRU(hidden_size, hidden_size, n_layers,
                          dropout=(0 if n_layers == 1 else dropout), bidirectional=True)

    def forward(self, input_seq, input_lengths, hidden=None):
        # Convert word indexes to embeddings
        embedded = self.embedding(input_seq)
        # Pack padded batch of sequences for RNN module
        packed = nn.utils.rnn.pack_padded_sequence(embedded, input_lengths)
        # Forward pass through GRU
        outputs, hidden = self.gru(packed, hidden)
        # Unpack padding
        outputs, _ = nn.utils.rnn.pad_packed_sequence(outputs)
        # Sum bidirectional GRU outputs
        outputs = outputs[:, :, :self.hidden_size] + outputs[:, : ,self.hidden_size:]
        # Return output and final hidden state
        return outputs, hidden

## Attention

In [42]:
# Luong attention layer
class Attn(nn.Module):
    def __init__(self, method, hidden_size):
        super(Attn, self).__init__()
        self.method = method
        if self.method not in ['dot', 'general', 'concat']:
            raise ValueError(self.method, "is not an appropriate attention method.")
        self.hidden_size = hidden_size
        if self.method == 'general':
            self.attn = nn.Linear(self.hidden_size, hidden_size)
        elif self.method == 'concat':
            self.attn = nn.Linear(self.hidden_size * 2, hidden_size)
            self.v = nn.Parameter(torch.FloatTensor(hidden_size))

    def dot_score(self, hidden, encoder_output):
        return torch.sum(hidden * encoder_output, dim=2)

    def general_score(self, hidden, encoder_output):
        energy = self.attn(encoder_output)
        return torch.sum(hidden * energy, dim=2)

    def concat_score(self, hidden, encoder_output):
        energy = self.attn(torch.cat((hidden.expand(encoder_output.size(0), -1, -1), encoder_output), 2)).tanh()
        return torch.sum(self.v * energy, dim=2)

    def forward(self, hidden, encoder_outputs):
        # Calculate the attention weights (energies) based on the given method
        if self.method == 'general':
            attn_energies = self.general_score(hidden, encoder_outputs)
        elif self.method == 'concat':
            attn_energies = self.concat_score(hidden, encoder_outputs)
        elif self.method == 'dot':
            attn_energies = self.dot_score(hidden, encoder_outputs)

        # Transpose max_length and batch_size dimensions
        attn_energies = attn_energies.t()

        # Return the softmax normalized probability scores (with added dimension)
        return F.softmax(attn_energies, dim=1).unsqueeze(1)

## Decoder

In [43]:
class LuongAttnDecoderRNN(nn.Module):
    def __init__(self, attn_model, embedding, hidden_size, output_size, n_layers=1, dropout=0.1):
        super(LuongAttnDecoderRNN, self).__init__()

        # Keep for reference
        self.attn_model = attn_model
        self.hidden_size = hidden_size
        self.output_size = output_size
        self.n_layers = n_layers
        self.dropout = dropout

        # Define layers
        self.embedding = embedding
        self.embedding_dropout = nn.Dropout(dropout)
        self.gru = nn.GRU(hidden_size, hidden_size, n_layers, dropout=(0 if n_layers == 1 else dropout))
        self.concat = nn.Linear(hidden_size * 2, hidden_size)
        self.out = nn.Linear(hidden_size, output_size)

        self.attn = Attn(attn_model, hidden_size)

    def forward(self, input_step, last_hidden, encoder_outputs):
        # Note: we run this one step (word) at a time
        # Get embedding of current input word
        embedded = self.embedding(input_step)
        embedded = self.embedding_dropout(embedded)
        # Forward through unidirectional GRU
        rnn_output, hidden = self.gru(embedded, last_hidden)
        # Calculate attention weights from the current GRU output
        attn_weights = self.attn(rnn_output, encoder_outputs)
        # Multiply attention weights to encoder outputs to get new "weighted sum" context vector
        context = attn_weights.bmm(encoder_outputs.transpose(0, 1))
        # Concatenate weighted context vector and GRU output using Luong eq. 5
        rnn_output = rnn_output.squeeze(0)
        context = context.squeeze(1)
        concat_input = torch.cat((rnn_output, context), 1)
        concat_output = torch.tanh(self.concat(concat_input))
        # Predict next word using Luong eq. 6
        output = self.out(concat_output)
        output = F.softmax(output, dim=1)
        # Return output and final hidden state
        return output, hidden

Define mask



In [44]:
def maskNLLLoss(inp, target, mask):
    nTotal = mask.sum()
    crossEntropy = -torch.log(torch.gather(inp, 1, target.view(-1, 1)).squeeze(1))
    loss = crossEntropy.masked_select(mask).mean()
    loss = loss.to(device)
    return loss, nTotal.item()

# Train

Initiating models

In [45]:
def train(input_variable, lengths, target_variable, mask, max_target_len, encoder, decoder, embedding,
          encoder_optimizer, decoder_optimizer, batch_size, clip, max_length=max_length):

    # Zero gradients
    encoder_optimizer.zero_grad()
    decoder_optimizer.zero_grad()

    # Set device options
    input_variable = input_variable.to(device)
    lengths = lengths.to(device)
    target_variable = target_variable.to(device)
    mask = mask.to(device)

    # Initialize variables
    loss = 0
    print_losses = []
    n_totals = 0

    # Forward pass through encoder
    encoder_outputs, encoder_hidden = encoder(input_variable, lengths)

    # Create initial decoder input (start with SOS tokens for each sentence)
    decoder_input = torch.LongTensor([[SOS_token for _ in range(batch_size)]])
    decoder_input = decoder_input.to(device)

    # Set initial decoder hidden state to the encoder's final hidden state
    decoder_hidden = encoder_hidden[:decoder.n_layers]

    # Determine if we are using teacher forcing this iteration
    use_teacher_forcing = True if random.random() < teacher_forcing_ratio else False

    # Forward batch of sequences through decoder one time step at a time
    if use_teacher_forcing:
        for t in range(max_target_len):
            decoder_output, decoder_hidden = decoder(
                decoder_input, decoder_hidden, encoder_outputs
            )
            # Teacher forcing: next input is current target
            decoder_input = target_variable[t].view(1, -1)
            # Calculate and accumulate loss
            mask_loss, nTotal = maskNLLLoss(decoder_output, target_variable[t], mask[t])
            loss += mask_loss
            print_losses.append(mask_loss.item() * nTotal)
            n_totals += nTotal
    else:
        for t in range(max_target_len):
            decoder_output, decoder_hidden = decoder(
                decoder_input, decoder_hidden, encoder_outputs
            )
            # No teacher forcing: next input is decoder's own current output
            _, topi = decoder_output.topk(1)
            decoder_input = torch.LongTensor([[topi[i][0] for i in range(batch_size)]])
            decoder_input = decoder_input.to(device)
            # Calculate and accumulate loss
            mask_loss, nTotal = maskNLLLoss(decoder_output, target_variable[t], mask[t])
            loss += mask_loss
            print_losses.append(mask_loss.item() * nTotal)
            n_totals += nTotal

    # Perform backpropatation
    loss.backward()

    # Clip gradients: gradients are modified in place
    _ = nn.utils.clip_grad_norm_(encoder.parameters(), clip)
    _ = nn.utils.clip_grad_norm_(decoder.parameters(), clip)

    # Adjust model weights
    encoder_optimizer.step()
    decoder_optimizer.step()

    return sum(print_losses) / n_totals

Training iterations

One thing to note is that when we save our model, we save a tarball
containing the encoder and decoder state_dicts (parameters), the
optimizers’ state_dicts, the loss, the iteration, etc. Saving the model
in this way will give us the ultimate flexibility with the checkpoint.
After loading a checkpoint, we will be able to use the model parameters
to run inference, or we can continue training right where we left off.

In [46]:
def train_model(model_name, vocab, pairs, encoder, decoder, encoder_optimizer, decoder_optimizer, embedding, encoder_n_layers, decoder_n_layers, save_dir, n_iteration, batch_size, print_every, save_every, clip, corpus_name, loadFilename):

    # Load batches for each iteration
    training_batches = [batch2TrainData(vocab, [random.choice(pairs) for _ in range(batch_size)])
                      for _ in range(n_iteration)]

    # Initializations
    print('Initializing ...')
    start_iteration = 1
    print_loss = 0
    if loadFilename:
        start_iteration = checkpoint['iteration'] + 1

    # Training loop
    print("Training model...")
    for iteration in range(start_iteration, n_iteration + 1):
        training_batch = training_batches[iteration - 1]
        # Extract fields from batch
        input_variable, lengths, target_variable, mask, max_target_len = training_batch

        # Run a training iteration with batch
        loss = train(input_variable, lengths, target_variable, mask, max_target_len, encoder,
                     decoder, embedding, encoder_optimizer, decoder_optimizer, batch_size, clip)
        print_loss += loss

        # Print progress
        if iteration % print_every == 0:
            print_loss_avg = print_loss / print_every
            print("Iteration: {}; Percent complete: {:.1f}%; Average loss: {:.4f}".format(iteration, iteration / n_iteration * 100, print_loss_avg))
            print_loss = 0

        # Save checkpoint
        if (iteration % save_every == 0):
            directory = os.path.join(save_dir, model_name, corpus_name, '{}-{}_{}'.format(encoder_n_layers, decoder_n_layers, hidden_size))
            if not os.path.exists(directory):
                os.makedirs(directory)
            torch.save({
                'iteration': iteration,
                'en': encoder.state_dict(),
                'de': decoder.state_dict(),
                'en_opt': encoder_optimizer.state_dict(),
                'de_opt': decoder_optimizer.state_dict(),
                'loss': loss,
                'vocab_dict': vocab.__dict__,
                'embedding': embedding.state_dict()
            }, os.path.join(directory, '{}_{}.tar'.format(iteration, 'checkpoint')))

Setting up model parameters 
---------

Not managed to include pre_trained embeddings, when embedding_size == hidden_size then it is easier to deal with multi-layer architecture because there is no need to treat  the first layers differently (accepting embeddings) from the successive layers (accepting hidden states)

In [56]:
# name the model is saved as
model_name = 'CNN_model_2'
# Set checkpoint to load from; set to None if starting from scratch
loadFilename = None
# Choose if using pre-trained Glove embeddings or not
pre_trained = False # this is not implemented
# Configure model paramters
attn_model = 'dot'
hidden_size = 300
encoder_n_layers = 4
decoder_n_layers = 4
dropout = 0.1
batch_size = 64

In [57]:
checkpoint_iter = 4000

#loadFilename = os.path.join(save_dir, model_name, corpus_name,
#                            '{}-{}_{}'.format(encoder_n_layers, decoder_n_layers, hidden_size),
#                            '{}_checkpoint.tar'.format(checkpoint_iter))


# Load model if a loadFilename is provided
if loadFilename:
    # If loading on same machine the model was trained on
    checkpoint = torch.load(loadFilename)
    # If loading a model trained on GPU to CPU
    #checkpoint = torch.load(loadFilename, map_location=torch.device('cpu'))
    encoder_sd = checkpoint['en']
    decoder_sd = checkpoint['de']
    encoder_optimizer_sd = checkpoint['en_opt']
    decoder_optimizer_sd = checkpoint['de_opt']
    embedding_sd = checkpoint['embedding']
    vocab.__dict__ = checkpoint['vocab_dict']


print('Building encoder and decoder ...')
embedding = nn.Embedding(vocab.num_words, hidden_size)

if loadFilename:
    embedding.load_state_dict(embedding_sd)
# Initialize encoder & decoder models
encoder = EncoderRNN(hidden_size, embedding, encoder_n_layers, dropout)
decoder = LuongAttnDecoderRNN(attn_model, embedding, hidden_size, vocab.num_words, decoder_n_layers, dropout)
if loadFilename:
    encoder.load_state_dict(encoder_sd)
    decoder.load_state_dict(decoder_sd)
# Use appropriate device
encoder = encoder.to(device)
decoder = decoder.to(device)
print('Finished building models.')

Building encoder and decoder ...
Finished building models.


# Training

In [58]:
# Configure training/optimization paramteters
clip = 50.0
teacher_forcing_ratio = 3.0
learning_rate = 0.001
decoder_learning_ratio = 5.0
n_iteration = 20000
print_every = 100
save_every = 500

In [59]:
# Ensure dropout layers are in train mode
encoder.train()
decoder.train()

# Initialize optimizers
print('Building optimizers ...')
encoder_optimizer = optim.Adam(encoder.parameters(), lr=learning_rate)
decoder_optimizer = optim.Adam(decoder.parameters(), lr=learning_rate * decoder_learning_ratio)
if loadFilename:
    encoder_optimizer.load_state_dict(encoder_optimizer_sd)
    decoder_optimizer.load_state_dict(decoder_optimizer_sd)

# If you have cuda, configure cuda to call
for state in encoder_optimizer.state.values():
    for k, v in state.items():
        if isinstance(v, torch.Tensor):
            state[k] = v.cuda()
            
for state in decoder_optimizer.state.values():
    for k, v in state.items():
        if isinstance(v, torch.Tensor):
            state[k] = v.cuda()
print('Finished building optimizers.')

Building optimizers ...
Finished building optimizers.


In [60]:
# Run training iterations
print("Starting Training...")
train_model(model_name, vocab, pairs, encoder, decoder, encoder_optimizer, decoder_optimizer,
           embedding, encoder_n_layers, decoder_n_layers, save_dir, n_iteration, batch_size,
           print_every, save_every, clip, 'CNN', loadFilename)

Starting Training...
Initializing ...
Training model...
Iteration: 100; Percent complete: 0.5%; Average loss: 7.8006
Iteration: 200; Percent complete: 1.0%; Average loss: 7.2734
Iteration: 300; Percent complete: 1.5%; Average loss: 6.6497
Iteration: 400; Percent complete: 2.0%; Average loss: 5.5963
Iteration: 500; Percent complete: 2.5%; Average loss: 4.4205
Iteration: 600; Percent complete: 3.0%; Average loss: 3.3788
Iteration: 700; Percent complete: 3.5%; Average loss: 2.6593
Iteration: 800; Percent complete: 4.0%; Average loss: 2.1476
Iteration: 900; Percent complete: 4.5%; Average loss: 1.7990
Iteration: 1000; Percent complete: 5.0%; Average loss: 1.5129
Iteration: 1100; Percent complete: 5.5%; Average loss: 1.2217
Iteration: 1200; Percent complete: 6.0%; Average loss: 0.9875
Iteration: 1300; Percent complete: 6.5%; Average loss: 0.8077
Iteration: 1400; Percent complete: 7.0%; Average loss: 0.6791
Iteration: 1500; Percent complete: 7.5%; Average loss: 0.6041
Iteration: 1600; Percen

Iteration: 13100; Percent complete: 65.5%; Average loss: 0.2598
Iteration: 13200; Percent complete: 66.0%; Average loss: 0.2582
Iteration: 13300; Percent complete: 66.5%; Average loss: 0.2579
Iteration: 13400; Percent complete: 67.0%; Average loss: 0.2529
Iteration: 13500; Percent complete: 67.5%; Average loss: 0.2570
Iteration: 13600; Percent complete: 68.0%; Average loss: 0.2534
Iteration: 13700; Percent complete: 68.5%; Average loss: 0.2564
Iteration: 13800; Percent complete: 69.0%; Average loss: 0.2661
Iteration: 13900; Percent complete: 69.5%; Average loss: 0.2531
Iteration: 14000; Percent complete: 70.0%; Average loss: 0.2558
Iteration: 14100; Percent complete: 70.5%; Average loss: 0.2569
Iteration: 14200; Percent complete: 71.0%; Average loss: 0.2506
Iteration: 14300; Percent complete: 71.5%; Average loss: 0.2487
Iteration: 14400; Percent complete: 72.0%; Average loss: 0.2575
Iteration: 14500; Percent complete: 72.5%; Average loss: 0.2635
Iteration: 14600; Percent complete: 73.0

## Testing

In [61]:
class GreedySearchDecoder(nn.Module):
    def __init__(self, encoder, decoder):
        super(GreedySearchDecoder, self).__init__()
        self.encoder = encoder
        self.decoder = decoder

    def forward(self, input_seq, input_length, max_length):
        # Forward input through encoder model
        encoder_outputs, encoder_hidden = self.encoder(input_seq, input_length)
        # Prepare encoder's final hidden layer to be first hidden input to the decoder
        decoder_hidden = encoder_hidden[:decoder.n_layers]
        # Initialize decoder input with SOS_token
        decoder_input = torch.ones(1, 1, device=device, dtype=torch.long) * SOS_token
        # Initialize tensors to append decoded words to
        all_tokens = torch.zeros([0], device=device, dtype=torch.long)
        all_scores = torch.zeros([0], device=device)
        # Iteratively decode one word token at a time
        for _ in range(max_length):
            # Forward pass through decoder
            decoder_output, decoder_hidden = self.decoder(decoder_input, decoder_hidden, encoder_outputs)
            # Obtain most likely word token and its softmax score
            decoder_scores, decoder_input = torch.max(decoder_output, dim=1)
            # Record token and score
            all_tokens = torch.cat((all_tokens, decoder_input), dim=0)
            all_scores = torch.cat((all_scores, decoder_scores), dim=0)
            # Prepare current token to be next decoder input (add a dimension)
            decoder_input = torch.unsqueeze(decoder_input, 0)
        # Return collections of word tokens and scores
        return all_tokens, all_scores

In [62]:
def evaluate(encoder, decoder, searcher, vocab, sentence, max_length=max_length):
    ### Format input sentence as a batch
    # words -> indexes
    indexes_batch = [indexesFromSentence(vocab, sentence)]
    # Create lengths tensor
    lengths = torch.tensor([len(indexes) for indexes in indexes_batch])
    # Transpose dimensions of batch to match models' expectations
    input_batch = torch.LongTensor(indexes_batch).transpose(0, 1)
    # Use appropriate device
    input_batch = input_batch.to(device)
    lengths = lengths.to(device)
    # Decode sentence with searcher
    tokens, scores = searcher(input_batch, lengths, max_length)
    # indexes -> words
    decoded_words = [vocab.index2word[token.item()] for token in tokens]
    return decoded_words

In [63]:
def evaluateInput(input_sentence, encoder, decoder, searcher, vocab):
    # Evaluate sentence
    output_words = evaluate(encoder, decoder, searcher, vocab, input_sentence)
    # Format and print response sentence
    output_words[:] = [x for x in output_words if not (x == EOS_str or x == PAD_str)]
    return ' '.join(output_words)

# Evaluation

Load the test file, print the original news article and the highlight togeather with the prediction.

In [64]:
import pandas as pd 

test_data = pd.read_csv(test_path) 
# Preview the first 5 lines of the loaded data 
test_data.head()

story  \
0  weddings happened count day federal judge stru...   
1  jurors convicted man three murders 2007 connec...   
2  man says behind manti teo girlfriend hoax clai...   
3  spoiler alert women getting cloned big twist e...   
4  florida man accused strangling family puppy ch...   

                                          highlights  
0  woman married in michigan says she expected th...  
1  new if he had life in prison that would be goi...  
2  new it was never going to be tuiasosopo says o...  
3  critically acclaimed series orphan black retur...  
4  police say thomas elliot huggins strangled and...

In [65]:
# Set dropout layers to eval mode
encoder.eval()
decoder.eval()

# Initialize search module
searcher = GreedySearchDecoder(encoder, decoder)

In [66]:
story, summary = test_data["story"].tolist(), test_data["highlights"].tolist()

In [67]:
for st,su in zip(story,summary):
    pr = evaluateInput(st,encoder, decoder, searcher, vocab)
    
    print("Story: ", st)
    print("Summary: ", su)
    print("---------------------------------------------------------------")
    print("Prediction: ", pr)
    print("---------------------------------------------------------------")

Story:  weddings happened count day federal judge struck michigan state amendment restricting marriage one man one woman gay lesbian couples lined saturday make unions official never thought would see day said ann watson wed partner 23 years sense amazing watson works turner broadcasting system entity includes cnn partner one 57 couples get sex marriage licenses ingham county according county clerk barb byrum byrum democrat elected county clerk post said personally performed 30 ceremonies mason today awesome day byrum tweeted county clerks followed suit taking abnormal step opening offices weekend others oakland county according cnn affiliate wdiv pontiac frank colasonti james ryder arrived early chance marry 26 years together colasonti told wdiv wanted get married soon possible wake court ruling issued late friday afternoon motivation simple love want make sure protect among first gay couples married michigan colasonti said historic glad part happy chance marriage could among last mic

Story:  spoiler alert women getting cloned big twist end orphan blacks second season kickoff new season leads list six things watch week ahead 1 orphan black 9 pm et saturday april 18 bbc america cloning cult sci fi series remains one critically acclaimed shows tv thanks large part performance tatiana maslany taken least six roles show far including newly introduced transgender clone maslany told reporters week expect even impressive scenes multiple clones like push boundaries able limits clone scenes said yes definitely see complex clone work season getting comfortable technology excited getting sort complicate things introduction group male clones certainly increase suspense definitely shift towards castor clones get explore little bit said fans show dubbed clone club lot look forward show premieres saturday 18th maslany blown away response series far always really humbled really inspired fans dedication show knowledge show changes lives incredible 2 turn washingtons spies 9 pm et mo

Story:  huddled around table hours handful top journalists cnns political unit poring youtube videos thousands republican hopefuls face wednesday cnn youtube debate laborious process necessary ensure best questions make cut cnn youtube debate republican presidential hopefuls st petersburg florida take place wednesday 8 pm et questions funny striking sad incredibly meaningful said sam feist cnns political director watch hundreds questions really get sense peoples minds cnn producers viewed 3500 video submissions people around world continue sifting submission deadline november 25 right debate 40 pass muster watch questions sent far second time debate taken place democratic candidates duked similar format past summer debate christened youtube venue prodding politicians way get public involved gop debate also face youtube audience expect hear questions debate let republican voters pick among eight candidates said david bohrman washington bureau chief senior vice president cnn trying focus

Story:  microsoft taking last big step releasing promises massive overhaul windows operating system extension almost devices running work nearing end long process tinkering hood computing giant friday rolled final preview windows 8 expected go sale fall since first preview release last september millions people use pre release product daily basis millions taking paces totaling hundreds millions hours testing microsofts steven sinofsky wrote friday windows 8 blog genuinely appreciate effort many put pre release testing course appreciate feedback direct feedback feedback usage contributed hundreds visible changes product tens thousands hood changes post said microsoft received 18000 comments 7000 early testers windows 8 contributed hundreds visible changes product tens thousands hood changes release mark first major update microsofts operating system since windows 7 released three years ago unlike previous releases essentially revamped least one case mercifully killed existing features m

Story:  deep south plunged deep freeze week time ice snow expected fall way gulf mexico forecasters issued winter storm warning new orleans suburbs monday afternoon warning city could see half inch snow ice tuesday evening parishes north could see three inches temperatures plunging single digits wednesday national weather service reported wave arctic air settled midwest plains expected spread southeast late monday bringing chance snow several major southern cities tuesday new orleans measurable snow fallen 17 times records date back 1880s french quarter restaurants made plans shut tourists worried stranded citys airport town shutting tomorrow cab driver august delaney told cnn bridges going shut schools closed going put kids school buses mayor mitch landrieu declared state emergency warned residents remember happened temperatures dipped toward freezing mark less week ago bridges frozen might remember landrieu said accidents bridges fairly large pile green bridge sometime long ago simil

...

Story:  sides us mexico border key questions lingering mexicos presidential vote election authorities projected enrique peña nieto institutional revolutionary party pri winner sunday night closest competitor andres manuel lopez obrador democratic revolution party prd conceded election results raise issues rooted mexicos complicated political past play critical role shaping nations future analysts say pri political party critics accuse authoritarian corrupt changed approach mexico lopez obrador supporters protest election results past peña nietos proposal decrease violence mark significant shift us mexico drug war policy mexicos old guard back local level may many differences todays pri political party dominated mexico decades said andrew selee director mexico institute woodrow wilson international center scholars changed national stage mexican citizens different expectations federal government going force pri govern different way 20 years ago selee said pri really party included mexico

Story:  three main uk party leaders gave joint promise tuesday scotland get extra powers opts stay part united kingdom landmark vote two days time opinion polls put pro independence pro union camps neck neck run thursdays referendum survival 300 year old union england scotland wales great britain knife edge uk prime minister david cameron conservatives coalition partner nick clegg liberal democrats labour leader ed miliband joined forces beg scotland stay pledge published front page scotlands daily record newspaper three leaders say scotlands voters reject independence work devolve extensive new powers central government westminster start friday issue spending social welfare health care national health service central pro independence campaign questions economy taxation also key promise leaders say state categorically final say much spent nhs matter scottish parliament conclude people want see change vote deliver faster safer better change separation lifetime opportunity huge turnout e

Story:  three years seesaw battles regime syrian rebels face another daunting challenge fending radical sunni militants taking swaths country islamic state iraq syria isis gained notoriety recent weeks group captured city city iraq goal create caliphate islamic state spanning iraq syria crises countries blending combined regional disaster isis controls land sides border opening floodgates weapons fighters syria iraq cities deir ezzor city iraq border stretch 90 miles 150 kilometers fallen isis said omar abu leila spokesman rebel free syrian army deir ezzor controlled partly government partly opposition militants said isis also took six syrian oil gas fields major pumping station distributes oil iraq syria abu leila said captures include al omar oil field syrias largest oil facility produce 75000 barrels oil day isis also seized military airport local army base land grabs isis stretch syrias deir ezzor province groups recently gained territories iraqs sunni heartland opposition syrian o

Story:  david beckham believes furore followed return la galaxy loan spell ac milan earlier year galvanized team galaxy mls western conference championship 2 0 win home houston dynamo friday night beckham setting gregg berhalters 102nd minute opener face real salt lake upset favored chicago fire 5 4 penalty shootout win eastern conference title saturday reach mls cup final seattle next sunday beckham subjected abuse fans missing start mls season italy galaxy captain landon donovan questioned commitment la franchise however england midfielder missed saturdays 1 0 friendly defeat brazil qatar play club thinks situation helped bring team together nothing wrong bit controversy club brings players teams together done beckham told espn post match interview say anything leave people decide love playing soccer work hard teammates manager fans hope enough people beckham joined galaxy real madrid 2007 struggled make impact englishmans time team arrival former usa national team coach bruce arena 

Story:  six months passenger ferry sank coast south korea victims body discovered inside wreckage tuesday body found fourth floor womens bathroom located center sunken sewol ferry according south korea joint task force charge search body retrieved yet due poor water visibility limited space search officials believe victim female nine victims remain missing ferry sank april 16 killing least 295 people underwater search continued months following disaster depending weather conditions officials said stop search operation unless families wish otherwise questions swirled could happen search winter approaches yonhap news agency south korea reported 102 days since last body recovered ferry ferry sank 195 days ago sewol disaster caused widespread outrage country lax safety standards failure rescue people ship foundered several members crew facing trial including captain learn verdict november 11 prosecutors seek death penalty ferry captain
Summary:  body found inside womens bathroom in sunken 